<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Open-Street-Map-API-geosearch" data-toc-modified-id="Open-Street-Map-API-geosearch-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Open Street Map API geosearch</a></span></li><li><span><a href="#Partial-updates" data-toc-modified-id="Partial-updates-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Partial updates</a></span></li></ul></div>

In [43]:
import requests
import pandas as pd
import json
import os, sys
import pandas_gbq
import plotly.express as px
from google.oauth2 import service_account


In [5]:
os.environ['GCP_SECRETPATH'] = '/Users/shuyili/Dropbox/data_assignments/secrets/my-user-project-287504-ef1a78f3e50d.json'
os.environ['GCP_PROJECID'] = 'my-user-project-287504'

In [6]:
def set_pandas_gbq_credentials():
    credentials = service_account.Credentials.from_service_account_file(os.environ['GCP_SECRETPATH'] )
    pandas_gbq.context.credentials = credentials
    pandas_gbq.context.project = os.environ['GCP_PROJECID'] 
set_pandas_gbq_credentials()

In [212]:
import time
tic=time.time()
df = pandas_gbq.read_gbq("""SELECT * FROM `my-user-project-287504.crime_statistics.dashboard` 
                    """, project_id=os.environ['GCP_PROJECID'])
toc=time.time()
print(toc-tic)

Downloading: 100%|██████████| 12652/12652 [00:01<00:00, 6949.18rows/s]

4.554497718811035


In [211]:
df.columns

Index(['id', 'language', 'datetime', 'city', 'type', 'summary', 'details',
       'location_details', 'gun_filter'],
      dtype='object')

In [28]:
import plotly.graph_objects as go

go.Layout(dict(margin=dict(l=30, r=30, b=20, t=40)))

Layout({
    'margin': {'b': 20, 'l': 30, 'r': 30, 't': 40}
})

In [235]:
# Creating and visualizing a scatter plot on Mapbox
mapbox_access_token='pk.eyJ1IjoiYWxjb2hvbGZyZWViZWFyIiwiYSI6ImNraW4yN3JhdjB5dmwyeHBrMmgxeXMzY3YifQ.hbyzFx6jjC10L4Vz8O5FLA'

layout = dict(
#     autosize=True,
#     automargin=True,
    margin=dict(l=30, r=30, b=20, t=40),
    hovermode="closest",
    plot_bgcolor="#F9F9F9",
    paper_bgcolor="#F9F9F9",
    legend=dict(font=dict(size=10), orientation="h"),
    title="Satellite Overview",
    mapbox=dict(
        accesstoken=mapbox_access_token,
        style="light",
        center=dict(lon=-78.05, lat=42.54),
        zoom=7,
    ),)


import numpy as np
px.set_mapbox_access_token(token=mapbox_access_token)
fig = px.scatter_mapbox(df, lat='osm_lat', lon='osm_lon',
                  #color= 'type', #size="Confirmed", size_max=70,
                  color_continuous_scale=px.colors.cyclical.IceFire,
                    size=np.ones(len(df)), size_max=10, zoom=4.5, hover_name='city', 
                  hover_data = ['datetime', 'city', 'type'],
                    mapbox_style='streets', opacity=0.5,
                  title = 'Accumulative incidents reported to police')
fig.update_layout(height=700, width=500, margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

### Open Street Map API geosearch

In [41]:
ss = df['location_details'].sample(100)

In [52]:


# 0.5 sec per request

results=[requests.get(osm_api_url(x)).text for x in ss.values]

['[{"place_id":99502447,"licence":"Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright","osm_type":"way","osm_id":32036539,"boundingbox":["60.6659983","60.6663592","16.9968268","17.0005245"],"lat":"60.6661633","lon":"16.9989682","display_name":"Norr Falltä, Lund, Gävle kommun, Gävleborgs län, 81834, Sverige","class":"highway","type":"residential","importance":0.3}]',
 '[{"place_id":37818246,"licence":"Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright","osm_type":"node","osm_id":2952106491,"boundingbox":["64.1315964","64.1715964","17.5932168","17.6332168"],"lat":"64.1515964","lon":"17.6132168","display_name":"Väster-Storsjö, Åsele kommun, Västerbottens län, Sverige","class":"place","type":"hamlet","importance":0.55,"icon":"https://nominatim.openstreetmap.org/ui/mapicons//poi_place_village.p.20.png"}]',
 '[]',
 '[]',
 '[{"place_id":1174469,"licence":"Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright","osm_type":"node","osm_id":

In [59]:
r=results[0]

In [98]:
def osm_api_url(search_term):
    return f"https://nominatim.openstreetmap.org/search/405 {search_term}?format=json&limit=1"

def get_osm_coord(row):
    result = requests.get(osm_api_url(row['location_details'])).text
    r_js=json.loads(result)
    if len(r_js)>0:
        r_js=r_js[0]
        return {**row, 'osm_lon':float(r_js['lon']), 'osm_lat':float(r_js['lat'])}
    else:
        return {**row, 'osm_lon':row['gps_lon'], 'osm_lat':row['gps_lat']}

In [120]:
requests.get(osm_api_url('Kävlinge Löddeköpinge Kävlinge Sweden')).text  #57.65000	12.016667	

'[{"place_id":183248055,"licence":"Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright","osm_type":"way","osm_id":394379693,"boundingbox":["55.7931262","55.7932746","12.9956208","12.9958314"],"lat":"55.7932004","lon":"12.995726099999995","display_name":"405, Landskronavägen, Hänkelstorp, Håkantorp, Löddeköpinge, Kävlinge kommun, Skåne län, 24643, Sverige","class":"building","type":"yes","importance":0.42100000000000004}]'

### Partial updates

In [94]:
sys.path.append('./app')
from operations import extract_keywords, extract_location_details, config

In [162]:
#ToDo: 
# city_refined
# 1. pull from bq
project_id=os.environ['GCP_PROJECID']
district = pandas_gbq.read_gbq(
        f"""SELECT * FROM `{project_id}.{config['dataset_id']}.dim_districts_hemnet`""", 
        project_id=project_id)
        

df = pandas_gbq.read_gbq("""SELECT * FROM `my-user-project-287504.crime_statistics.raw`""", project_id=project_id)


                    
# extract location details again
def process_newly_arrived(newly_arrived):
    print(newly_arrived.shape)
    newly_arrived_list=[]
    for city in newly_arrived.location_name.unique():
        newly_arrived_i=newly_arrived[newly_arrived['location_name']==city]
        details_list = newly_arrived_i['details']+' '+newly_arrived_i['summary']+' '+ newly_arrived_i['name']
        newly_arrived_i['location_details'] = [extract_location_details(detail, district=district[district['city']==city]) for detail in details_list]
        newly_arrived_i['location_details'] = newly_arrived_i['location_details'] +' ' +newly_arrived_i['location_name']+' ' +'Sweden'
        newly_arrived_list.append(newly_arrived_i)
    newly_arrived=pd.concat(newly_arrived_list)
    # get osm coordinates
    rows=[]
    for _, row in newly_arrived.iterrows():
        rows.append(get_osm_coord(row.copy()))
    newly_arrived_upload=pd.DataFrame(rows)
    return newly_arrived_upload
refined=process_newly_arrived(df)

# deduplicate
refined=refined.sort_values(by='date_requested', ascending=False).groupby(['id'])[[ 'date_requested', 'datetime', 'details', 'gps', 'gps_lat', 'gps_lon',
        'location_details', 'location_name', 'name', 'osm_lat', 'osm_lon',
       'summary', 'type', 'url']].first().reset_index()

# upload to bq
       
pandas_gbq.to_gbq(refined,'crime_statistics.cities_refined', project_id=project_id, if_exists='replace' )

Downloading: 100%|██████████| 6375/6375 [00:01<00:00, 5036.36rows/s]


(6375, 12)


/opt/anaconda3/envs/env-ml-opencv/lib/python3.7/site-packages/ipykernel_launcher.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

/opt/anaconda3/envs/env-ml-opencv/lib/python3.7/site-packages/ipykernel_launcher.py:22: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

1it [00:08,  8.11s/it]


In [126]:
# city_refined_en
# 1. pull from bq

en = pandas_gbq.read_gbq("""SELECT * FROM `my-user-project-287504.crime_statistics.cities_refined_en` 
                    """, project_id=os.environ['GCP_PROJECID'])
# get osm coordinates by mapping using id
en = en.sort_values(by='date_requested', ascending=False).groupby(['id'])[[ 'date_requested', 'datetime', 'details', 'gps', 'gps_lat', 'gps_lon',
        'location_details', 'location_name', 'name', #'osm_lat', 'osm_lon',
       'summary', 'type', 'url']].first().reset_index()
print(en.shape)
en['osm_lat']=en['id'].map(dict(refined[['id', 'osm_lat']].to_records(index=False)))
en['osm_lon']=en['id'].map(dict(refined[['id', 'osm_lon']].to_records(index=False)))
pandas_gbq.to_gbq(refined,'crime_statistics.cities_refined_en', project_id=project_id, if_exists='replace' )

# upload to bq

Downloading: 100%|██████████| 6375/6375 [00:01<00:00, 4503.06rows/s]


In [134]:
print(refined.shape)
refined.columns

(6350, 15)


Index(['date_requested', 'datetime', 'details', 'gps', 'gps_lat', 'gps_lon',
       'id', 'location_details', 'location_name', 'name', 'osm_lat', 'osm_lon',
       'summary', 'type', 'url'],
      dtype='object')

In [135]:
print(en.shape)

en.columns

(6375, 13)


Index(['datetime', 'id', 'name', 'summary', 'type', 'url', 'location_name',
       'gps', 'gps_lat', 'gps_lon', 'date_requested', 'details',
       'location_details'],
      dtype='object')

In [159]:
en_new = en[['id']].drop_duplicates()

In [160]:
en_new.shape

(6326, 1)

In [148]:
refined = refined.groupby(['datetime', 'details', 'gps', 'gps_lat', 'gps_lon',
       'id', 'location_details', 'location_name', 'name', 'osm_lat', 'osm_lon',
       'summary', 'type', 'url'])[['date_requested']].max().reset_index()


In [145]:
refined.set_index(['id', 'datetime'])[refined.groupby(['id', 'datetime']).size()>1]

/opt/anaconda3/envs/env-ml-opencv/lib/python3.7/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date_requested  \
id     datetime                                                     
231814 2020-10-20 14:41:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 14:41:00+00:00 2020-10-20 17:50:04.131547+00:00   
231769 2020-10-20 07:10:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 07:10:00+00:00 2020-10-20 17:50:04.131547+00:00   
231830 2020-10-20 15:06:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 15:06:00+00:00 2020-10-20 17:50:04.131547+00:00   
231800 2020-10-20 12:40:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 12:40:00+00:00 2020-10-20 17:50:04.131547+00:00   
231834 2020-10-20 15:06:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 15:06:00+00:00 2020-10-20 17:50:04.131547+00:00   
231767 2020-10-20 11:44:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 11:44:00+00:00 2020-10-20 17:50:04.131547+00:00   
231825 2020-10-20 14:27:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 14:27:00+00:00 2020-10-20 17:50:04.131547+00:00   
231787 2020-10-20 13:02:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 13:02:00+00:00 2020-10-20 17:50:04.131547+00:00   
231813 2020-10-20 14:25:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 14:25:00+00:00 2020-10-20 17:50:04.131547+00:00   
231809 2020-10-20 14:23:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 14:23:00+00:00 2020-10-20 17:50:04.131547+00:00   
231826 2020-10-20 16:22:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 16:22:00+00:00 2020-10-20 17:50:04.131547+00:00   
231807 2020-10-20 12:09:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 12:09:00+00:00 2020-10-20 17:50:04.131547+00:00   
231785 2020-10-20 11:51:00+00:00 2020-10-20 19:50:12.256367+00:00   
231823 2020-10-20 15:17:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 15:17:00+00:00 2020-10-20 17:50:04.131547+00:00   
231785 2020-10-20 11:51:00+00:00 2020-10-20 17:50:04.131547+00:00   
231828 2020-10-20 13:54:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 13:54:00+00:00 2020-10-20 17:50:04.131547+00:00   
...                                                           ...   
231820 2020-10-20 15:34:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 15:34:00+00:00 2020-10-20 17:50:04.131547+00:00   
231796 2020-10-20 12:58:00+00:00 2020-10-20 19:50:12.256367+00:00   
231794 2020-10-20 12:31:00+00:00 2020-10-20 19:50:12.256367+00:00   
231832 2020-10-20 15:35:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 15:35:00+00:00 2020-10-20 17:50:04.131547+00:00   
231794 2020-10-20 12:31:00+00:00 2020-10-20 17:50:04.131547+00:00   
231796 2020-10-20 12:58:00+00:00 2020-10-20 17:50:04.131547+00:00   
231816 2020-10-20 10:22:00+00:00 2020-10-20 19:50:12.256367+00:00   
231818 2020-10-20 11:43:00+00:00 2020-10-20 19:50:12.256367+00:00   
231816 2020-10-20 10:22:00+00:00 2020-10-20 17:50:04.131547+00:00   
231818 2020-10-20 11:43:00+00:00 2020-10-20 17:50:04.131547+00:00   
231824 2020-10-20 15:08:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 15:08:00+00:00 2020-10-20 17:50:04.131547+00:00   
231822 2020-10-20 13:40:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 13:40:00+00:00 2020-10-20 17:50:04.131547+00:00   
231817 2020-10-20 12:22:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 12:22:00+00:00 2020-10-20 17:50:04.131547+00:00   
231831 2020-10-20 16:28:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 16:28:00+00:00 2020-10-20 17:50:04.131547+00:00   
231806 2020-10-20 14:17:00+00:00 2020-10-20 19:50:12.256367+00:00   
       2020-10-20 14:17:00+00:00 2020-10-20 17:50:04.131547+00:00   
231829 2020-10-20 16:45:00+00:00 2020-10-20 19:50:12.256367+00:00   
231801 2020-10-20 14:06:00+00:00 2020-10-20 19:50:12.256367+00:00   
231829 2020-10-20 16:45:00+00:00 2020-10-20 17:50:04.131547+00:00   
231801 2020-10-20 14:06:00+00:00 2020-10-20 17:50

In [161]:
en.set_index('id').loc[list(set(en.id)-set(refined.id))]

datetime  \
id                                 
235011 2020-11-11 20:45:00+00:00   
235012 2020-11-11 20:45:00+00:00   
233485 2020-10-31 15:21:00+00:00   
233486 2020-10-31 15:30:00+00:00   
234510 2020-11-08 15:01:00+00:00   
234000 2020-11-04 20:44:00+00:00   
234001 2020-11-04 20:45:00+00:00   
234511 2020-11-08 15:01:00+00:00   
235539 2020-11-15 10:35:00+00:00   
239635 2020-12-10 13:50:00+00:00   
232469 2020-10-24 14:00:00+00:00   
240032 2020-12-13 12:49:00+00:00   
232471 2020-10-24 14:00:00+00:00   
235037 2020-11-12 05:54:00+00:00   
235038 2020-11-12 05:54:00+00:00   
235039 2020-11-12 05:53:00+00:00   
236575 2020-11-23 20:45:00+00:00   
236576 2020-11-23 20:46:00+00:00   
230434 2020-10-17 13:45:00+00:00   
230435 2020-10-17 13:45:00+00:00   
234022 2020-11-05 02:13:00+00:00   
234025 2020-11-05 06:18:00+00:00   
240033 2020-12-13 08:29:00+00:00   
237933 2020-12-02 07:18:00+00:00   
236078 2020-11-20 03:11:00+00:00   
234543 2020-11-09 06:42:00+00:00   
237934 2020-12-02 07:18:00+00:00   
239159 2020-12-07 20:45:00+00:00   
239160 2020-12-07 20:46:00+00:00   
234050 2020-11-05 08:11:00+00:00   
...                          ...   
235427 2020-11-15 13:35:00+00:00   
235428 2020-11-15 13:36:00+00:00   
235429 2020-11-15 11:56:00+00:00   
235430 2020-11-15 13:18:00+00:00   
235431 2020-11-15 13:45:00+00:00   
235432 2020-11-15 14:51:00+00:00   
230316 2020-10-16 14:48:00+00:00   
235433 2020-11-15 14:52:00+00:00   
232366 2020-10-23 20:00:00+00:00   
232367 2020-10-23 20:00:00+00:00   
235436 2020-11-15 15:58:00+00:00   
234929 2020-11-11 10:37:00+00:00   
235437 2020-11-15 16:02:00+00:00   
235438 2020-11-15 14:48:00+00:00   
235439 2020-11-15 18:26:00+00:00   
235440 2020-11-15 18:45:00+00:00   
235441 2020-11-15 19:00:00+00:00   
235442 2020-11-15 22:21:00+00:00   
235443 2020-11-15 22:22:00+00:00   
236976 2020-11-26 11:44:00+00:00   
230330 2020-10-16 16:37:00+00:00   
239028 2020-12-07 05:55:00+00:00   
233405 2020-10-30 20:46:00+00:00   
233406 2020-10-30 20:47:00+00:00   
239042 2020-12-07 07:43:00+00:00   
239043 2020-12-07 07:43:00+00:00   
231876 2020-10-21 05:00:00+00:00   
233929 2020-11-04 13:43:00+00:00   
235475 2020-11-15 20:05:00+00:00   
233455 2020-10-31 10:10:00+00:00   

                                                     name  \
id                                                          
235011    11 november 21:45, Övrigt, Västra Götalands län   
235012            11 november 21:45, Övrigt, Hallands län   
233485     31 oktober 16:21, Övrigt, Västra Götalands län   
233486             31 oktober 16:30, Övrigt, Hallands län   
234510    08 november 16:01, Övrigt, Västra Götalands län   
234000    04 november 21:44, Övrigt, Västra Götalands län   
234001            04 november 21:45, Övrigt, Hallands län   
234511            08 november 16:01, Övrigt, Hallands län   
235539            15 november 11:35, Stöld/inbrott, Gävle   
239635          10 december 14:50, Trafikbrott, Stockholm   
232469     24 oktober 16:00, Övrigt, Västra Götalands län   
240032   13 december 13:49, Trafikolycka, singel, Varberg   
232471             24 oktober 16:00, Övrigt, Hallands län   
235037  12 november 06:54, Sammanfattning natt, Örebro...   
235038  12 november 06:54, Sammanfattning natt, Värmla...   
235039  12 november 06:53, Sammanfattning natt, Dalarn...   
236575    23 november 21:45, Övrigt, Västra Götalands län   
236576            23 november 21:46, Övrigt, Hallands län   
230434     17 oktober 15:45, Övrigt, Västra Götalands län   
230435             17 oktober 15:45, Övrigt, Hallands län   
234022        05 november 03:13, Stöld/inbrott, Stockholm   
234025  05 november 07:18, Sammanfattning natt, Örebro...   
240033       13 december 09:29, Övrigt, Södermanlands län   
237933    02 december 08:18, Övrigt, Västra Götalands län   
236078  20 november 04:11, Sammanfattning natt, Väster...   
234543                 09 november 07:42, Brand, Botkyrka   
237934            02 december 08:18, Övrigt, Ha